### Import libraries and read data

In [2]:
%load_ext autoreload
%autoreload 2


In [3]:
import pandas as pd
import geopandas as gpd
import altair as alt
from scipy import stats

from helpers import apply_style
alt.data_transformers.disable_max_rows()

regions = gpd.read_file("data/NEONDomains_0/NEON_Domains.shp")
md_ee = pd.read_csv("data/NEON_metadata_ee_2.csv")
md_geo = gpd.GeoDataFrame(
    geometry=gpd.points_from_xy(md_ee.longitude, md_ee.latitude, crs="EPSG:4326"), data=md_ee
)

joined = md_geo.sjoin(regions[['DomainID','DomainName','OBJECTID','geometry']], how='left')

### EDA
* check distributions of EO indices

In [4]:
l = ['NBR_mean', 'NBR_p10', 'NBR_p90', 'NBR_stdDev',
       'NDMI_mean', 'NDMI_p10', 'NDMI_p90', 'NDMI_stdDev', 'NDVI_mean',
       'NDVI_p10', 'NDVI_p90', 'NDVI_stdDev', 'ND_GREEN_RED_mean',
       'ND_GREEN_RED_p10', 'ND_GREEN_RED_p90', 'ND_GREEN_RED_stdDev',
       'RED_SWIR_RATIO_mean', 'RED_SWIR_RATIO_p10', 'RED_SWIR_RATIO_p90',
       'RED_SWIR_RATIO_stdDev', 'SAVI_mean', 'SAVI_p10', 'SAVI_p90',
       'SAVI_stdDev']
cl = [alt.Chart(joined).mark_bar().encode(
    x=alt.X(i, bin=alt.Bin(extent=[-1, 1.5], step=0.05), title=i),
    y='count()'
) for i in l]
o = alt.hconcat(*cl)
o

alt.HConcatChart(...)

In [5]:

ndvi_m = alt.Chart(joined).mark_bar().encode(
    x=alt.X('NDVI_mean', bin=alt.Bin(extent=[-1, 1.5], step=0.05), title="NDVI_mean"),
    y='count()'
)
ndvi_p10 = alt.Chart(joined).mark_bar().encode(
    x=alt.X('NDVI_p10', bin=alt.Bin(extent=[-1, 1], step=0.05), title="NDVI_p10"),
    y='count()'
)
ndvi_p90 = alt.Chart(joined).mark_bar().encode(
    x=alt.X('NDVI_p90', bin=alt.Bin(extent=[-1, 1], step=0.05), title="NDVI_p90"),
    y='count()'
)

chart2 = ndvi_m | ndvi_p10 | ndvi_p90
apply_style(chart2,'Distributions of NDVI at sample sites','2018 - mean, 10th percentile, 90th percentile')

alt.HConcatChart(...)

### Calculate correlation 

In [6]:

cormat = joined[['NBR_mean', 'NBR_p10', 'NBR_p90', 'NBR_stdDev',
       'NDMI_mean', 'NDMI_p10', 'NDMI_p90', 'NDMI_stdDev', 'NDVI_mean',
       'NDVI_p10', 'NDVI_p90', 'NDVI_stdDev', 'ND_GREEN_RED_mean',
       'ND_GREEN_RED_p10', 'ND_GREEN_RED_p90', 'ND_GREEN_RED_stdDev',
       'RED_SWIR_RATIO_mean', 'RED_SWIR_RATIO_p10', 'RED_SWIR_RATIO_p90',
       'RED_SWIR_RATIO_stdDev', 'SAVI_mean', 'SAVI_p10', 'SAVI_p90',
       'SAVI_stdDev','fungal_diversity']].corr()
round(cormat,2)

NBR_mean  NBR_p10  NBR_p90  NBR_stdDev  NDMI_mean  \
NBR_mean                   1.00     0.91     0.90        0.03       0.95   
NBR_p10                    0.91     1.00     0.67       -0.38       0.80   
NBR_p90                    0.90     0.67     1.00        0.43       0.92   
NBR_stdDev                 0.03    -0.38     0.43        1.00       0.17   
NDMI_mean                  0.95     0.80     0.92        0.17       1.00   
NDMI_p10                   0.92     0.95     0.73       -0.24       0.90   
NDMI_p90                   0.81     0.53     0.96        0.53       0.91   
NDMI_stdDev                0.05    -0.35     0.45        0.98       0.20   
NDVI_mean                  0.30     0.46     0.10       -0.41       0.04   
NDVI_p10                   0.24     0.44     0.00       -0.51      -0.03   
NDVI_p90                   0.38     0.47     0.23       -0.27       0.14   
NDVI_stdDev                0.21    -0.00     0.40        0.51       0.33   
ND_GREEN_RED_mean          0.72     0.63     0.67        0.08       0.65   
ND_GREEN_RED_p10           0.70     0.66     0.57       -0.06       0.60   
ND_GREEN_RED_p90           0.70     0.57     0.70        0.18       0.64   
ND_GREEN_RED_stdDev        0.05    -0.12     0.30        0.49       0.11   
RED_SWIR_RATIO_mean        0.72     0.58     0.76        0.23       0.84   
RED_SWIR_RATIO_p10         0.74     0.74     0.61       -0.13       0.80   
RED_SWIR_RATIO_p90         0.49     0.24     0.74        0.57       0.64   
RED_SWIR_RATIO_stdDev      0.22    -0.09     0.58        0.77       0.37   
SAVI_mean                  0.40     0.52     0.20       -0.37       0.14   
SAVI_p10                   0.31     0.50     0.07       -0.50       0.05   
SAVI_p90                   0.46     0.53     0.32       -0.23       0.24   
SAVI_stdDev                0.27     0.02     0.47        0.56       0.39   
fungal_diversity           0.19     0.19     0.13       -0.04       0.16   

                       NDMI_p10  NDMI_p90  NDMI_stdDev  NDVI_mean  NDVI_p10  \
NBR_mean                   0.92      0.81         0.05       0.30      0.24   
NBR_p10                    0.95      0.53        -0.35       0.46      0.44   
NBR_p90                    0.73      0.96         0.45       0.10      0.00   
NBR_stdDev                -0.24      0.53         0.98      -0.41     -0.51   
NDMI_mean                  0.90      0.91         0.20       0.04     -0.03   
NDMI_p10                   1.00      0.67        -0.22       0.24      0.21   
NDMI_p90                   0.67      1.00         0.57      -0.15     -0.25   
NDMI_stdDev               -0.22      0.57         1.00      -0.46     -0.55   
NDVI_mean                  0.24     -0.15        -0.46       1.00      0.98   
NDVI_p10                   0.21     -0.25        -0.55       0.98      1.00   
NDVI_p90                   0.28     -0.02        -0.33       0.95      0.88   
NDVI_stdDev                0.12      0.46         0.49      -0.23     -0.42   
ND_GREEN_RED_mean          0.61      0.55         0.06       0.46      0.38   
ND_GREEN_RED_p10           0.63      0.45        -0.09       0.50      0.45   
ND_GREEN_RED_p90           0.57      0.60         0.16       0.41      0.31   
ND_GREEN_RED_stdDev       -0.07      0.34         0.50      -0.12     -0.23   
RED_SWIR_RATIO_mean        0.75      0.82         0.24      -0.21     -0.25   
RED_SWIR_RATIO_p10         0.86      0.62        -0.14      -0.01     -0.01   
RED_SWIR_RATIO_p90         0.41      0.82         0.59      -0.33     -0.40   
RED_SWIR_RATIO_stdDev      0.06      0.68         0.80      -0.41     -0.48   
SAVI_mean                  0.32     -0.04        -0.41       0.88      0.86   
SAVI_p10                   0.28     -0.17        -0.52       0.88      0.90   
SAVI_p90                   0.36      0.09        -0.27       0.82      0.76   
SAVI_stdDev                0.15      0.54         0.53      -0.23     -0.40   
fungal_diversity           0.17      0.09        -0.05       0.20      

In [7]:
corr_matrix = cormat.stack().reset_index()
corr_matrix.columns = ['variable1', 'variable2', 'correlation']


heatmap = alt.Chart(corr_matrix).mark_rect().encode(
    x=alt.X('variable1:N',title=None),
    y=alt.Y('variable2:N', title=None),
    color=alt.Color('correlation:Q', title=None).scale(scheme='spectral')
)
text = heatmap.mark_text(baseline='middle', fontSize=8).encode(
    alt.Text('correlation:Q', format=".2f"),
    color=alt.condition(
        abs(alt.datum.correlation) > 0.75,
        alt.value('white'),
        alt.value('black')
    )
)
both = heatmap + text
both.properties(width=800, height=800)
apply_style(heatmap + text ,"","")

alt.LayerChart(...)

### Results

In [15]:
mvd = alt.Chart(joined,  width=500).mark_point(opacity=0.65, filled=True).encode(
    x=alt.X('NDVI_p90').title('NDVI 90th Percentile'),
    y=alt.Y('fungal_diversity').title("Fungal Diversity"),
    color=alt.Color('DomainName').scale(scheme='category20b')
    
)
line = mvd.transform_regression('NDVI_p90', 'fungal_diversity', method='linear').mark_line().encode(
     color=alt.value("red"))

apply_style((mvd+line), "fungal diversity against NDVI", "sentinel 2 - 2018 NDVI 90th percentile")

alt.LayerChart(...)

In [9]:
joined_nn = joined.dropna(how='any').copy() # drop nulls
stats.pearsonr(joined_nn.NDVI_p90,joined_nn.fungal_diversity)

PearsonRResult(statistic=0.23578762991006783, pvalue=3.995612170562056e-21)